# **First and Second Waves Comparison**

>Since the beginning of the pandemic, several Covid-19 mutations, also known as *variants*, have appeared. \\
Among them, the Brazilian variant is said to be a more severe form of Covid-19 by many scientists worldwide. \\
In a process to validate the veracity of this hypothesis or not, this Notebook proposes a study and comparison of the current two main waves, involving the same parts of population. \\
During these waves, the same parts of the population were subject. The idea is to find what are the key factors in the most severe waves, to conclude if the lethality of the Brazilian variant is higher or not.

## Libraries

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy.integrate import odeint
from scipy import optimize
import plotly.graph_objects as go
import yaml
from datetime import datetime
from sklearn import metrics as mt

## SIRD model

In [2]:
# The SIRD model differential equations.
def SIRD(y, t, N, Beta, Gamma, Mu):
    S, I, R, D = y
    dSdt = -(Beta * I * S)/N
    dIdt = (Beta * I * S)/N  - Gamma * I - Mu * I
    dRdt = Gamma * I
    dDdt = Mu * I
    return dSdt, dIdt, dRdt, dDdt

In [3]:
#Saving the simulation results

def SIRDsim(y0, t, N, theta):
  
  #Transmission rate
  Beta = theta[0]
  #Recovery rate per day
  Gamma = theta[1]
  #Mortality rate
  Mu = theta[2]

  # Integrate the SIRD equations over the time grid t.
  result = odeint(SIRD, y0, t, args=(N, Beta, Gamma, Mu))
  S, I, R, D = result.T
  return S, I, R, D

In [4]:
#Least Squares Method

def QuadraticError(theta0, Sd, Id, Rd, Dd, y0, t, N):
    """ function to pass to optimize.leastsq
        The routine will square and sum the values returned by 
        this function""" 
    [S,I,R,D] = SIRDsim(y0, t, N, theta0)
    errorS = S - Sd
    errorI = I - Id
    errorR = R - Rd
    errorD = D - Dd
    EQ = np.concatenate([errorI,errorR,errorD])
    return EQ

## Fitting Automation

> To analyze and fit the SIRD model to different waves, the previous model has to be updated, adding a starting and an ending points to the parameters research.

In [5]:
def SIRD_state_fitting_algorithm(State_Name, theta0, T0=0, Tf=200, Tsim=300):
  """This function is fitting the SIRD model to a Dataset
     and plots the resulting curves.
     Args:
           - State_Name: Abbreviated name of a State  | string
           - theta0: Initial parameters               | tuple of float Beta, Gamma, Mu
           - T0: Starting point of the study          | int (days)
           - Tf: Ending point of the study            | int (days)
           - Tsim: Simulation duration                | int (days) 
  """

  # Reading data - wcota
  data_path = 'https://raw.githubusercontent.com/wcota/covid19br/master/cases-brazil-states.csv'
  df = pd.read_csv(data_path, delimiter=",") 

  # Dataframe for the specific State
  df_state = df[df.state == State_Name].reset_index()

  # Creating new recovered column
  df_state["newRecovered"] = df_state["recovered"].diff()
  df_state.newRecovered.fillna(0, inplace=True)
  df_state.recovered.fillna(0, inplace=True)

  # Creating active cases column (Infected)
  active_infected = [df_state["totalCases"].iloc[0]]
  for nc, nr in zip(df_state["newCases"].iloc[1:], 
                    df_state["newRecovered"].iloc[1:]):
      active_infected.append(active_infected[-1] + nc - nr)
  df_state["activeCases"] = active_infected

  # State population
  with open('/content/drive/MyDrive/ISMIN/Semestre 8/Stage International/Instituto Maua de Tecnologia/Maua Internship/05_Notebooks/DataSets/state_pop.yaml') as f:
    state_pop = yaml.load(f)

  if (State_Name != 'TOTAL'):
    N = state_pop[State_Name]['population']

    #Susceptible population
    alpha = (df_state["recovered"][T0+Tsim] + df_state["activeCases"][T0+Tsim] + df_state["deaths"][T0+Tsim])/N
    N = alpha*N
  else:
    N = (df_state["recovered"][T0+Tsim] + df_state["activeCases"][T0+Tsim] + df_state["deaths"][T0+Tsim])
  
  # Considering the research duration for the parameters
  df_state_init = df_state.iloc[T0:Tf]
  
  # Data
  Id = df_state_init["activeCases"]
  Rd = df_state_init["recovered"]
  Dd = df_state_init["deaths"]
  Sd = N - Rd - Id - Dd

  # Initial Conditions
  I0 = df_state_init["activeCases"][T0]
  R0 = df_state_init["recovered"][T0]
  D0 = df_state_init["deaths"][T0]
  S0 = N - (I0 + R0 + D0)
  y0 = S0, I0, R0, D0


  # Time vector
  t = np.linspace(0, len(df_state_init.index.values), len(df_state_init.index.values))

  # Model use to find optimal parameters
  (best_theta, kvg) = optimize.leastsq(QuadraticError, theta0, args=(Sd,Id,Rd,Dd,y0,t,N))

  # Fitted simulation
  df_state_sim = df_state.iloc[T0:T0+Tsim] # Days of simulation
  tsim = np.linspace(0, len(df_state_sim.index.values), len(df_state_sim.index.values))
  [Ss,Is,Rs,Ds] = SIRDsim(y0, tsim, N, best_theta)

  # Shaping data
  Data_df = df_state.iloc[:(T0+Tsim)]
  timeline = Data_df['date']
  I = Data_df['activeCases']
  R = Data_df['recovered']
  D = Data_df['deaths']
  S = N - (I+R+D)

  data = {'Date': timeline, 'Sd': S, 'Id': I, 'Rd': R, 'Dd': D}

  Final_df = pd.DataFrame(data)

  Sim_index_vector = range(T0,T0+Tsim)

  Final_df['Ss'] = pd.DataFrame(Ss, Sim_index_vector)
  Final_df['Is'] = pd.DataFrame(Is, Sim_index_vector)
  Final_df['Rs'] = pd.DataFrame(Rs, Sim_index_vector)
  Final_df['Ds'] = pd.DataFrame(Ds, Sim_index_vector)

  return Final_df

In [6]:
def SIRD_plotting(SIRD_df):
  # Plotting the results

  Sd,Id,Rd,Dd = SIRD_df['Sd'], SIRD_df['Id'], SIRD_df['Rd'], SIRD_df['Dd']
  Ss,Is,Rs,Ds = SIRD_df['Ss'], SIRD_df['Is'], SIRD_df['Rs'], SIRD_df['Ds']
  timeline = SIRD_df['Date']

  fig = go.Figure()

  fig.add_trace(go.Scatter(
      name="Active Cases - Model",
      x=timeline,
      y=Is,
      mode='lines',
      line=dict(width=3, dash="dash", color="#6a1b9a")
      ))

  fig.add_trace(go.Scatter(
      name="Recovered - Model",
      x=timeline,
      y=Rs,
      mode='lines',
      line=dict(width=3, dash="dash", color="#2e7d32")
      ))

  fig.add_trace(go.Scatter(
      name="Susceptible - Model",
      x=timeline,
      y=Ss,
      mode='lines',
      line=dict(width=3, dash="dash", color="#58ACFA")
      ))

  fig.add_trace(go.Scatter(
      name="Desceased - Model",
      x=timeline,
      y=Ds,
      mode='lines',
      line=dict(width=3, dash="dash", color="burlywood")
      ))

  fig.add_trace(go.Scatter(
      name="Active Cases - Data",
      x=timeline,
      y=Id,
      mode='markers',
      marker=dict(size=4, color="#38006b")
      ))
  
  fig.add_trace(go.Scatter(
      name="Recovered - Data",
      x=timeline,
      y=Rd,
      mode='markers',
      marker=dict(size=4, color="#005005")
      ))

  fig.add_trace(go.Scatter(
      name="Susceptible - Data",
      x=timeline,
      y=Sd,
      mode='markers',
      marker=dict(size=4, color="#0080FF")
      ))

  fig.add_trace(go.Scatter(
      name="Desceased - Data",
      x=timeline,
      y=Dd,
      mode='markers',
      marker=dict(size=4, color="burlywood")
      ))
  
  fig.update_layout(
      template='xgridoff',
      xaxis=dict(showgrid=False),
      xaxis_title='Days',
      yaxis_title='Individuals',
      legend=dict(
        orientation='h',
        yanchor='bottom',
        y=1.01,
        xanchor='right',
        x=0.95
        ),
      title_text="SIRD Model")

  fig.show()

## States 1st and 2nd Waves

### Acre

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('AC', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:16 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('AC', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:16 using Wesley Cota Database


### Alagoas

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('AL', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:17 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('AL', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:18 using Wesley Cota Database


### Amapá

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('AP', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:18 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('AP', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:19 using Wesley Cota Database


### Amazonas

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('AM', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:20 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('AM', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:20 using Wesley Cota Database


### Bahia

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('BA', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:21 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('BA', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:22 using Wesley Cota Database


### Ceará

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('CE', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:22 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('CE', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:23 using Wesley Cota Database


### Distrito Federal

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('DF', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:24 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('DF', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:24 using Wesley Cota Database


### Espírito Santo

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('ES', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:25 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('ES', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:25 using Wesley Cota Database


### Goiás

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('GO', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:26 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('GO', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:27 using Wesley Cota Database


### Maranhão

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('MA', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:27 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('MA', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:28 using Wesley Cota Database


### Mato Grosso

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('MT', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:29 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('MT', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:30 using Wesley Cota Database


### Mato Grosso do Sul

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('MS', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:30 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('MS', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:32 using Wesley Cota Database


### Minas Gerais

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('MG', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:33 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('MG', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:34 using Wesley Cota Database


### Pará

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('PA', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:35 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('PA', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:36 using Wesley Cota Database


### Paraíba

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('PB', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:36 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('PB', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:37 using Wesley Cota Database


### Paraná

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('PR', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:38 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('PR', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:38 using Wesley Cota Database


### Pernambuco

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('PE', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:39 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('PE', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:40 using Wesley Cota Database


### Piauí

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('PI', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:40 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('PI', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:41 using Wesley Cota Database


### Rio de Janeiro

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('RJ', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:42 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('RJ', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:42 using Wesley Cota Database


### Rio Grande do Norte

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('RN', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:43 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('RN', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:44 using Wesley Cota Database


### Rio Grande do Sul

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('RS', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:44 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('RS', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:45 using Wesley Cota Database


### Rondônia

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('RO', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:46 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('RO', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:46 using Wesley Cota Database


### Roraima

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('RR', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:47 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('RR', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:48 using Wesley Cota Database


### Santa Catarina

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('SC', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:48 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('SC', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:49 using Wesley Cota Database


### São Paulo

#### 1st Wave

In [16]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('SP', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:50 using Wesley Cota Database


#### 2nd Wave

In [23]:
SIRD_plotting(SIRD_state_fitting_algorithm('SP', theta0, 250, 480, 230))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:50 using Wesley Cota Database


### Sergipe

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('SE', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:51 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('SE', theta0, 200, 400, 200))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:51 using Wesley Cota Database


### Tocantins

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('TO', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:52 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('TO', theta0, 300, 400, 110))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:04:53 using Wesley Cota Database


## Brazil's 1st and 2nd Waves

#### 1st Wave

In [ ]:
# Initial Parameters
theta0 = [0.4, 0.1, 0.002]

SIRD_plotting(SIRD_state_fitting_algorithm('TOTAL', theta0))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:15:58 using Wesley Cota Database


#### 2nd Wave

In [ ]:
SIRD_plotting(SIRD_state_fitting_algorithm('TOTAL', theta0, 300, 400, 100))

In [ ]:
simulation_time = datetime.now().strftime("%d/%m/%Y at %H:%M:%S")
print("Simulation done the", simulation_time, "using Wesley Cota Database")

Simulation done the 06/05/2021 at 16:15:58 using Wesley Cota Database


## Conclusion

>>As a conclusion, the tools to study the current 1st and 2nd waves are created. \\
The following of the study is now to analyze the results and draw relevant conclusions concerning the waves' caracteristics, especially the lethality to validate or not the hypothesis of a more lethal Brazilian variant. 